In [16]:
import re
import csv
import os

# 正则表达式模式
pattern = re.compile(
    r'(?P<authors>[\w\s,.]+),\s*"'  # 匹配作者名字，可能包含逗号和点号
    r'(?P<title>[^"]+),"\s*'        # 匹配文章标题，不包括双引号
    r'(?P<year>\d{4})'         # 匹配年份，四位数字
    r'\s+(IEEE\s+International\s+Conference\s+on\s+Robotics\s+and\s+Automation\s+\(ICRA\)|IEEE/RSJ\s+International\s+Conference\s+on\s+Intelligent\s+Robots\s+and\s+Systems\s+\(IROS\)),' # r'\s+Yokohama,\s+Japan,'          # 可选的会议地点，匹配逗号和任意非逗号字符
    # r'\s+([^,]+),\s+([^,]+),'
    r'\s+(([^,]+),\s+([^,]+)|([^,]+),\s+([^,]+),\s+([^,]+)),'
    r'\s+(?P=year),'           # 匹配年份，确保与前面一致
    r'\s+pp\.\s+\d+-\d+,'      # 匹配页码范围
    r'\s+doi:\s+\d+\.+\d+/(ICRA+\d{5}\.+\d{4}\.+\d{8}|IROS+\d{5}\.+\d{4}\.+\d{8})\.'   # 匹配DOI
    r'Abstract:\s+'          # 匹配“.Abstract:”
    r'(?P<abstract>.*?)'       # 匹配摘要，非贪婪匹配
    r'\s+keywords:\s+\{'       # 匹配“keywords: {”
    r'(?P<keywords>[^}]+)},'     # 匹配关键词，不包括右花括号
    r'URL:\s'           # 匹配“}, URL:”
    r'(?P<url>https://ieeexplore\.ieee\.org/[^"]+)'  # 匹配URL
    , re.DOTALL                # 允许点号匹配换行符
)

# 存储提取的信息
papers = []
# paper_dir = 'icra2023'
# paper_dir = 'iros2023'
paper_dir = 'icra2024'
# 读取文本文件
txt_files = [file for file in os.listdir(f'./{paper_dir}/') if file.endswith('.txt')]

for txt_file in txt_files:
    with open(os.path.join(f'./{paper_dir}/', txt_file), 'r', encoding='utf-8') as file:
        text = file.read()
        # 逐行匹配提取信息
        for line in text.splitlines():
            if line.strip():
                print(line)
                match = pattern.search(line)
                if match:
                    print(match.group('authors'))
                    print(match.group('title'))
                    print(match.group('year'))
                    print(match.group('abstract').strip())
                    print(match.group('keywords'))
                    print(match.group('url'))
                    paper = {
                        'title': match.group('title'),
                        'authors': match.group('authors').split(', '),
                        'year': match.group('year'),
                        'abstract': match.group('abstract').strip(),
                        'keywords': match.group('keywords').split(';'),
                        'url': match.group('url')
                    }
                    papers.append(paper)
                else:
                    print('Not match!------')

# 将信息保存到CSV文件
with open('papers.csv', 'w', newline='', encoding='utf-8') as csvfile:
    fieldnames = ['title', 'authors', 'year', 'abstract', 'keywords', 'url']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for paper in papers:
        writer.writerow({
            'title': paper['title'],
            'authors': ', '.join(paper['authors']),
            'year': paper['year'],
            'abstract': paper['abstract'],
            'keywords': ', '.join(paper['keywords']),
            'url': paper['url']
        })

print(f"{len(papers)}信息已成功提取并保存到 {paper_dir}.csv 文件中。")

C. Gall, W. Fichter and A. Ahmad, "End-to-End Thermal Updraft Detection and Estimation for Autonomous Soaring Using Temporal Convolutional Networks," 2024 IEEE International Conference on Robotics and Automation (ICRA), Yokohama, Japan, 2024, pp. 17875-17881, doi: 10.1109/ICRA57147.2024.10611479.Abstract: Exploiting thermal updrafts to gain altitude can significantly extend the endurance of fixed-wing aircraft, as has been demonstrated by human glider pilots for decades. In this work, we present a novel end-to-end deep learning approach for the simultaneous detection of multiple thermal updrafts and the estimation of their properties — a key capability to let autonomous unmanned aerial vehicles soar as well. In contrast to previous works, our approach does not require separate algorithms for the detection of individual updrafts. Instead, a sequence of sensor measurements from a time window of interest can be directly fed into our temporal convolutional network, which estimates the posi


J. Wang et al., "WeatherDepth: Curriculum Contrastive Learning for Self-Supervised Depth Estimation under Adverse Weather Conditions," 2024 IEEE International Conference on Robotics and Automation (ICRA), Yokohama, Japan, 2024, pp. 4976-4982, doi: 10.1109/ICRA57147.2024.10611100.Abstract: Depth estimation models have shown promising performance on clear scenes but fail to generalize to adverse weather conditions due to illumination variations, weather particles, etc. In this paper, we propose WeatherDepth, a self-supervised robust depth estimation model with curriculum contrastive learning, to tackle performance degradation in complex weather conditions. Concretely, we first present a progressive curriculum learning scheme with three simple-to-complex curricula to gradually adapt the model from clear to relative adverse, and then to adverse weather scenes. It encourages the model to gradually grasp beneficial depth cues against the weather effect, yielding smoother and better domain a

In [17]:
# 生成HTML文件
with open(f'{paper_dir}.html', 'w', encoding='utf-8') as htmlfile:
    htmlfile.write('''
    <!DOCTYPE html>
    <html lang="en">
    <head>
        <meta charset="UTF-8">
        <meta name="viewport" content="width=device-width, initial-scale=1.0">
        <title>Papers</title>
        <style>
            table {
                width: 100%;
                border-collapse: collapse;
            }
            th, td {
                border: 1px solid #ddd;
                padding: 8px;
                word-wrap: break-word;
                max-width: 200px;
            }
            th {
                background-color: #f2f2f2;
            }
            td:nth-child(4) {
                width: 50%; /* 使abstract列的宽度是其他列的两倍 */
            }
        </style>
    </head>
    <body>
        <h1>Papers</h1>
        <table>
            <tr>
                <th>Title</th>
                <th>Authors</th>
                <th>Year</th>
                <th>Abstract</th>
                <th>Keywords</th>
                <th>URL</th>
            </tr>
    ''')

    for paper in papers:
        htmlfile.write(f'''
            <tr>
                <td>{paper['title']}</td>
                <td>{', '.join(paper['authors'])}</td>
                <td>{paper['year']}</td>
                <td>{paper['abstract']}</td>
                <td>{', '.join(paper['keywords'])}</td>
                <td><a href="{paper['url']}">{paper['url']}</a></td>
            </tr>
        ''')

    htmlfile.write('''
        </table>
    </body>
    </html>
    ''')

print(f"信息已成功提取并保存到 {paper_dir}.html 文件中。")

信息已成功提取并保存到 icra2024.html 文件中。
